In [90]:
import pandas as pd
import numpy as np
from matplotlib import pyplot as plt
from matplotlib import ticker
import seaborn as sns
import json
import datetime 

from plotly.offline import init_notebook_mode, iplot
init_notebook_mode(connected=True)
import plotly.graph_objs as go
import plotly.express as px

In [91]:
df_path = "./USvideos.csv"

In [92]:
df = pd.read_csv(df_path)

In [93]:
df

video_id trending_date  \
0      2kyS6SvSYSE      17.14.11   
1      1ZAPwfrtAFY      17.14.11   
2      5qpjK5DgCt4      17.14.11   
3      puqaWrEC7tY      17.14.11   
4      d380meD0W0M      17.14.11   
...            ...           ...   
40944  BZt0qjTWNhw      18.14.06   
40945  1h7KV2sjUWY      18.14.06   
40946  D6Oy4LfoqsU      18.14.06   
40947  oV0zkMe1K8s      18.14.06   
40948  ooyjaVdt-jA      18.14.06   

                                                   title  \
0                     WE WANT TO TALK ABOUT OUR MARRIAGE   
1      The Trump Presidency: Last Week Tonight with J...   
2      Racist Superman | Rudy Mancuso, King Bach & Le...   
3                       Nickelback Lyrics: Real or Fake?   
4                               I Dare You: GOING BALD!?   
...                                                  ...   
40944                       The Cat Who Caught the Laser   
40945                         True Facts : Ant Mutualism   
40946  I GAVE SAFIYA NYGAARD A PERFECT HAIR MAKEOVER ...   
40947                How Black Panther Should Have Ended   
40948  Official Call of Duty®: Black Ops 4 — Multipla...   

                  channel_title  category_id              publish_time  \
0                  CaseyNeistat           22  2017-11-13T17:13:01.000Z   
1               LastWeekTonight           24  2017-11-13T07:30:00.000Z   
2                  Rudy Mancuso           23  2017-11-12T19:05:24.000Z   
3         Good Mythical Morning           24  2017-11-13T11:00:04.000Z   
4                      nigahiga           24  2017-11-12T18:01:41.000Z   
...                         ...          ...                       ...   
40944             AaronsAnimals           15  2018-05-18T13:00:04.000Z   
40945                  zefrank1           22  2018-05-18T01:00:06.000Z   
40946                Brad Mondo           24  2018-05-18T17:34:22.000Z   
40947  How It Should Have Ended            1  2018-05-17T17:00:04.000Z   
40948              Call of Duty           20  2018-05-17T17:09:38.000Z   

                                                    tags     views   likes  \
0                                        SHANtell martin    748374   57527   
1      last week tonight trump presidency|"last week ...   2418783   97185   
2      racist superman|"rudy"|"mancuso"|"king"|"bach"...   3191434  146033   
3      rhett and link|"gmm"|"good mythical morning"|"...    343168   10172   
4      ryan|"higa"|"higatv"|"nigahiga"|"i dare you"|"...   2095731  132235   
...                                                  ...       ...     ...   
40944  aarons animals|"aarons"|"animals"|"cat"|"cats"...   1685609   38160   
40945                                             [none]   1064798   60008   
40946  I gave safiya nygaard a perfect hair makeover ...   1066451   48068   
40947  Black Panther|"HISHE"|"Marvel"|"Infinity War"|...   5660813  192957   
40948      call of duty|"cod"|"activision"|"Black Ops 4"  10306119  357079   

       dislikes  comment_count  \
0          2966          15954   
1          6146          12703   
2          5339           8181   
3           666           2146   
4          1989          17518   
...         ...            ...   
40944      1385           2657   
40945       382           3936   
40946      1032           3992   
40947      2846          13088   
40948    212976         144795   

                                       thumbnail_link  comments_disabled  \
0      https://i.ytimg.com/vi/2kyS6SvSYSE/default.jpg              False   
1      https://i.ytimg.com/vi/1ZAPwfrtAFY/default.jpg              False   
2      https://i.ytimg.com/vi/5qpjK5DgCt4/default.jpg              False   
3      https://i.ytimg.com/vi/puqaWrEC7tY/default.jpg              False   
4      https://i.ytimg.com/vi/d380meD0W0M/default.jpg              False   
...                                               ...                ...   
40944  https://i.ytimg.com/vi/BZt0qjTWNhw/default.jpg              False   
40945  https:

In [94]:
df['like/dislike'] = (df['likes']/df['dislikes'])

In [95]:
with open("datasets_4549_466349_US_category_id.json") as datafile:
    categories = json.load(datafile)["items"]

categories_dict = {}
for category in categories:
    categories_dict[int(category["id"])] = category["snippet"]["title"]
df['category_name'] = df['category_id'].map(categories_dict)

In [96]:
fig = px.box(df, x="category_name", y="like/dislike", color="category_name", 
             title="Distribution of like-dislike ratio wrt video category",
             labels={
                     "category_name": "Video category",
                     "like/dislike": "Like-Dislike ratio",
                     "category_name": "Video category"
             })

fig.update_layout(
    xaxis=dict(showgrid=False, zeroline=False, showticklabels=False),
    yaxis=dict(zeroline=False, gridcolor='white', range=[0,220]),
    paper_bgcolor='rgb(233,233,233)',
    plot_bgcolor='rgb(233,233,233)',
)

fig.show()

In [97]:
# Change trending_date format to a more manageable format
df['trending_date'] = pd.to_datetime(df['trending_date'], format='%y.%d.%m')

# Extract the day and hour from date
df['publishing_day'] = df['publish_time'].apply(lambda x: pd.to_datetime(x[:10], format='%Y-%m-%d'))
df['publishing_hour'] = df['publish_time'].apply(lambda x: x[11:13])

# Remove duplicate videos
df = df.sort_values('trending_date').drop_duplicates('video_id', keep='first')
    
# Calculate window between the video's publishing date and the date it trended
df['time_to_trend'] = (df['trending_date'] - df['publishing_day']).dt.days

# remove videos with negative time to trend time
df = df[df.time_to_trend >= 0]

In [98]:
df

video_id trending_date  \
0      2kyS6SvSYSE    2017-11-14   
127    htvR_dBs3eg    2017-11-14   
128    qEEtzzi1EII    2017-11-14   
129    1Wk8ZRgXQnY    2017-11-14   
130    8l_e6bx8UG8    2017-11-14   
...            ...           ...   
40760  dS5Thrl-4Kc    2018-06-14   
40761  JGm9Y_hFqNk    2018-06-14   
40762  6h8QgZF5Qu4    2018-06-14   
40764  mpnshdmtE2Y    2018-06-14   
40766  yz7Xq3T0YPs    2018-06-14   

                                                   title  \
0                     WE WANT TO TALK ABOUT OUR MARRIAGE   
127        Sam Smith - The Thrill of It All ALBUM REVIEW   
128                   Birthdays - Simon's Cat | GUIDE TO   
129       Andy Grammer - The Good Parts (Official Audio)   
130            Remy Ma - Wake Me Up (Audio) ft. Lil' Kim   
...                                                  ...   
40760                      CRAYOLA MAKEUP | HIT OR MISS?   
40761  First Take reacts: Kyrie Irving says contract ...   
40762  Drop the Mic w/ Ashton Kutcher & Sean Diddy Combs   
40764  Carla Makes BA Smashburgers | From the Test Ki...   
40766  Katherine Langford on 13 Reasons Why, Australi...   

                              channel_title  category_id  \
0                              CaseyNeistat           22   
127                           theneedledrop           10   
128                             Simon's Cat           15   
129                            Andy Grammer           10   
130                              RemyMaVEVO           10   
...                                     ...          ...   
40760                             Laura Lee           26   
40761                                  ESPN           17   
40762  The Late Late Show with James Corden           24   
40764                           Bon Appétit           26   
40766                     Jimmy Kimmel Live           24   

                   publish_time  \
0      2017-11-13T17:13:01.000Z   
127    2017-11-10T21:38:57.000Z   
128    2017-11-09T13:34:58.000Z   
129    2017-11-09T22:27:45.000Z   
130    2017-11-08T17:00:00.000Z   
...                         ...   
40760  2018-06-12T18:55:26.000Z   
40761  2018-06-13T15:06:08.000Z   
40762  2018-06-13T05:27:27.000Z   
40764  2018-06-12T16:03:58.000Z   
40766  2018-06-13T09:00:06.000Z   

                                                    tags    views  likes  \
0                                        SHANtell martin   748374  57527   
127    album|"review"|"music"|"reviews"|"indie"|"unde...    98422   2926   
128    cartoon|"simons cat"|"simon's cat"|"simonscat"...   426078  19323   
129    andy|"grammer"|"the"|"good"|"parts"|"smoke"|"c...    33315   1365   
130    Columbia|"Hip Hop"|"Remy Ma feat. Lil' Kim"|"W...  1231518  32648   
...                                                  ...      ...    ...   
40760  Laura88Lee|"crayola"|"crayon makeup"|"crayola ...   607422  26166   
40761  espn|"espn live"|"boston celtics"|"kyrie irvin...   812832   7701   
40762  The Late Late Show|"Late Late Show"|"James Cor...   864189  18811   
40764  bon appetit|"burgers"|"cheeseburgers"|"how to ...   540149  14206   
40766  jimmy|"kimmel"|"live"|"late"|"night"|"talk"|"s...   296295   8157   

       dislikes  ...                                  thumbnail_link  \
0          2966  ...  https://i.ytimg.com/vi/2kyS6SvSYSE/default.jpg   
127         106  ...  https://i.ytimg.com/vi/htvR_dBs3eg/default.jpg   
128         245  ...  https://i.ytimg.com/vi/qEEtzzi1EII/default.jpg   
129          24  ...  https://i.ytimg.com/vi/1Wk8ZRgXQnY/default.jpg   
130        6221  ...  https://i.ytimg.com/vi/8l_e6bx8UG8/default.jpg   
...         ...  ...                                             ...   
40760       895  ...  https://i.ytimg.com/vi/dS5Thrl-4Kc/default.jpg   
40761       320  ...  https://i.ytimg.com/vi/JGm9Y_hFqNk/default.jpg   
40762       399  ...  https://i.ytimg.com/vi/6h8QgZF5Qu4/default.jpg   
40764       693  ...  https://i.ytimg.com/vi/mpnshdmtE2Y/default.jpg   
40766    

In [99]:
fig = px.box(df, x="category_name", y="time_to_trend", color="category_name", 
             title="Time the video of a category takes to go trending",
             labels={
                     "category_name": "Video category",
                     "time_to_trend": "Days taken to go trending",
                     "category_name": "Video category"
             })

fig.update_layout(
    xaxis=dict(showgrid=False, zeroline=False, showticklabels=False),
    yaxis=dict(zeroline=False, gridcolor='white', range=[0,8.5]),
    paper_bgcolor='rgb(233,233,233)',
    plot_bgcolor='rgb(233,233,233)',
)

fig.show()

In [103]:
fig = px.bar(df, x="category_name", y="like/dislike", 
             title="Distribution of like-dislike ratio wrt video category",
             labels={
                     "category_name": "Video category",
                     "like/dislike": "Like-Dislike ratio",
                     "category_name": "Video category"
             })

fig.show()

In [81]:
tdf = df['channel_title'].value_counts().head(15)

data = [go.Bar(x=tdf.values, y=tdf.index.values, orientation='h')]

iplot(data, filename='jupyter-basic_bar')

In [8]:
with open("datasets_4549_466349_US_category_id.json") as datafile:
    categories = json.load(datafile)["items"]

categories_dict = {}
for category in categories:
    categories_dict[int(category["id"])] = category["snippet"]["title"]
df['category_name'] = df['category_id'].map(categories_dict)

In [75]:
tdf = df['category_name'].value_counts().head(15)

data = [go.Bar(x=tdf.values, y=tdf.index.values, orientation='h')]

iplot(data, filename='jupyter-basic_bar')